# Лабораторная работа №3

## Набор данных Students Performance in Exams (Успеваемость студентов на экзаменах)

Выгрузка данных из CSV файла в датафрейм

In [178]:
import pandas as pd
# Загрузка данных
df = pd.read_csv("..//..//static//csv//StudentsPerformance.csv")

random_state=9

### Описание набора  

Контекст
Оценки, полученные студентами

Содержание
Этот набор данных состоит из оценок, полученных учащимися по различным предметам.

Вдохновение
Понять влияние происхождения родителей, подготовки к тестированию и т. д. на успеваемость учащихся.

### Анализ содержимого

*Объекты наблюдения:* студенты, участвующие в экзаменах.

*Атрибуты объектов:* 

1. gender — пол: определяет гендерную принадлежность студента (мужской, женский).  
2. race/ethnicity — этническая принадлежность: группа, к которой относится студент (например, различные расовые/этнические категории).  
3. parental level of education — уровень образования родителей(например, среднее образование, высшее образование и т.д.).  
4. lunch — тип обеда: информация о том, получает ли студент бесплатный или платный обед.  
5. test preparation course — курс подготовки к тесту
6. math score  — результаты экзаменов по математике.
7. reading score — результаты экзаменов по чтению.
8. writing score — результаты экзаменов по письму.


### Бизнес-цель:

**Цель**: Прогнозирование успеваемости студентов на основе различных факторов, таких как пол, раса/этническая принадлежность, уровень образования родителей, тип обеда и участие в подготовительных курсах.  

**Эффект**: Предсказание результатов студентов позволяет выявить тех, кто может столкнуться с трудностями в учебе. Это дает возможность образовательным учреждениям предпринимать превентивные меры: например, организовывать дополнительные занятия, персонализированные консультации, улучшать условия обучения и даже вмешиваться на более ранних стадиях, чтобы повысить общий уровень успеваемости.


### Техническая цель
**Цель**: Создание регрессионной модели, которая будет предсказывать общий балл студентов (или другой числовой показатель успеваемости) на основе категориальных и числовых данных. Это потребует использования методов линейной или нелинейной регрессии для определения зависимости между признаками (пол, уровень образования родителей и т.д.) и итоговым баллом.  

**Подход**: Для решения задачи нужно использовать числовые признаки, такие как "math score", "reading score", "writing score", и выполнить их агрегацию (например, суммирование или среднее), чтобы построить прогноз для общего балла. Модели, такие как линейная регрессия или регрессия на основе деревьев решений, подойдут для этого. у которых ожидаются низкие результаты на экзаменах, тем самым повышая их шансы на успешную сдачу экзаменов.


### Конструирование признаков для решения задач

Можно создать новый признак, который будет представлять общую успеваемость студента. Например, можно суммировать баллы по всем предметам и создать общий балл. 


In [179]:
df['total_score'] = df['math score'] + df['reading score'] + df['writing score']
df = df.drop(columns=['math score', 'reading score', 'writing score'])


#### Выберем три модели для задач регрессии

1. Линейная регрессия служит базовой моделью, чтобы понять, насколько линейны зависимости между признаками и целевой переменной. Это важный шаг для проверки простых гипотез.

2. Случайный лес используется для обработки данных с более сложными зависимостями, когда данные могут содержать нелинейные связи, которые линейная регрессия не может уловить.

3. Градиентный бустинг — это более сложная модель, которая позволяет добиться высокой точности, особенно при наличии сложных закономерностей в данных. Он может предложить лучшее качество прогноза при оптимальной настройке гиперпараметров.

Эти три модели дадут нам хорошее сочетание простоты (линейная регрессия), гибкости (случайный лес) и мощности (градиентный бустинг), что позволит тщательно исследовать зависимости и добиться хорошего качества предсказаний.

#### Разделение набора данных на обучающую и тестовые выборки (80/20) для задачи регрессии и создание ориентира

Целевой признак -- total_score

In [180]:
from sklearn.model_selection import train_test_split

# Разбиение на признаки и целевую переменную
X = df.drop(columns=["total_score"])  # Признаки
y = df["total_score"]  # Целевая переменная

# Разбиение на обучающую и тестовую выборки
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=random_state)

#### Формирование конвейера

In [181]:
from sklearn.compose import ColumnTransformer
from sklearn.discriminant_analysis import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder

# Пайплайн для обработки признаков
columns_to_drop = ["total_score"]
num_columns = [column for column in X.columns if X[column].dtype != "object"]
cat_columns = [column for column in X.columns if X[column].dtype == "object"]

# Обработчики для числовых и категориальных признаков
num_imputer = SimpleImputer(strategy="median")
num_scaler = StandardScaler()
preprocessing_num = Pipeline([("imputer", num_imputer), ("scaler", num_scaler)])

cat_imputer = SimpleImputer(strategy="constant", fill_value="unknown")
cat_encoder = OneHotEncoder(handle_unknown="ignore", sparse_output=False, drop="first")
preprocessing_cat = Pipeline([("imputer", cat_imputer), ("encoder", cat_encoder)])

# Обрабатываем признаки
features_preprocessing = ColumnTransformer(
    transformers=[
        ("prepocessing_num", preprocessing_num, num_columns),
        ("prepocessing_cat", preprocessing_cat, cat_columns),
    ],
    remainder="passthrough"
)

#### Настройка гиперпараметров для каждой модели и обучение

In [182]:
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

# 1. Линейная регрессия
linear_model = LinearRegression()

# Параметры для настройки
linear_param_grid = {
    'model__fit_intercept': [True, False],  # Использовать ли свободный член
}

# 2. Случайный лес
rf_model = RandomForestRegressor(random_state=random_state)

# Параметры для настройки
rf_param_grid = {
    'model__n_estimators': [50, 100, 200],
    'model__max_depth': [None, 10, 20],
    'model__min_samples_split': [2, 5],
    'model__min_samples_leaf': [1, 2],
    'model__max_features': ['sqrt', 'log2'],  # Заменить 'auto' на 'sqrt'
}

# 3. Градиентный бустинг
gb_model = GradientBoostingRegressor(random_state=random_state)

# Параметры для настройки
gb_param_grid = {
    'model__n_estimators': [50, 100, 200],  # Количество деревьев
    'model__learning_rate': [0.01, 0.1, 0.2],  # Темп обучения
    'model__max_depth': [3, 5, 7],  # Максимальная глубина деревьев
}

# Создание пайплайна для линейной регрессии
linear_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("model", linear_model)
])

# Создание пайплайна для случайного леса
rf_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("model", rf_model)
])

# Создание пайплайна для градиентного бустинга
gb_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("model", gb_model)
])

# Настройка гиперпараметров с использованием GridSearchCV
linear_search = GridSearchCV(linear_pipeline, linear_param_grid, cv=5, n_jobs=-1)
rf_search = GridSearchCV(rf_pipeline, rf_param_grid, cv=5, n_jobs=-1)
gb_search = GridSearchCV(gb_pipeline, gb_param_grid, cv=5, n_jobs=-1)

# Обучение моделей
linear_search.fit(X_train, y_train.values.ravel())  # Преобразуем y_train в одномерный массив
rf_search.fit(X_train, y_train.values.ravel())  # Преобразуем y_train в одномерный массив
gb_search.fit(X_train, y_train.values.ravel())  # Преобразуем y_train в одномерный массив


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('features_preprocessing',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('prepocessing_num',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('scaler',
                                                                                          StandardScaler())]),
                                                                         []),
                                                                        ('prepocessing_cat',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(fill_value='unknown',
                                                                                                        strategy='constant')),
                                                                                         ('enc...
                                                                                          OneHotEncoder(drop='first',
                                                                                                        handle_unknown='ignore',
                                                                                                        sparse_output=False))]),
                                                                         ['gender',
                                                                          'race/ethnicity',
                                                                          'parental '
                                                                          'level '
                                                                          'of '
                                                                          'education',
                                                                          'lunch',
                                                                          'test '
                                                                          'preparation '
                                                                          'course'])])),
                                       ('model',
                                        GradientBoostingRegressor(random_state=9))]),
             n_jobs=-1,
             param_grid={'model__learning_rate': [0.01, 0.1, 0.2],
                         'model__max_depth': [3, 5, 7],
                         'model__n_estimators': [50, 100, 200]})

#### Оценка качества моделей

Для оценки качества моделей будем использовать следующие метрики:

R^2 — это классическая метрика для оценки качества модели в регрессии. Она покажет, насколько хорошо модель объясняет данные, и полезна, чтобы понять, имеет ли смысл использовать модель.

MAE и MSE — они дают представление о точности модели и масштабах ошибок. MAE поможет понять средний уровень ошибки, а MSE и RMSE — сосредоточатся на более крупных ошибках, что может быть критично для задач, где крупные ошибки имеют большое значение.

RMSE полезна в контексте конкретных приложений, когда важно понять ошибку в тех же единицах, что и целевая переменная, особенно если данные в регрессии имеют четкую физическую или экономическую интерпретацию.

In [183]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

# Прогнозы для каждой модели
y_pred_linear = linear_search.predict(X_test)
y_pred_rf = rf_search.predict(X_test)
y_pred_gb = gb_search.predict(X_test)

# R^2
r2_linear = r2_score(y_test, y_pred_linear)
r2_rf = r2_score(y_test, y_pred_rf)
r2_gb = r2_score(y_test, y_pred_gb)

# MAE
mae_linear = mean_absolute_error(y_test, y_pred_linear)
mae_rf = mean_absolute_error(y_test, y_pred_rf)
mae_gb = mean_absolute_error(y_test, y_pred_gb)

# MSE
mse_linear = mean_squared_error(y_test, y_pred_linear)
mse_rf = mean_squared_error(y_test, y_pred_rf)
mse_gb = mean_squared_error(y_test, y_pred_gb)

# RMSE
rmse_linear = mse_linear ** 0.5
rmse_rf = mse_rf ** 0.5
rmse_gb = mse_gb ** 0.5

# Вывод результатов
print(f"Linear Regression - R^2: {r2_linear}, MAE: {mae_linear}, MSE: {mse_linear}, RMSE: {rmse_linear}")
print(f"Random Forest - R^2: {r2_rf}, MAE: {mae_rf}, MSE: {mse_rf}, RMSE: {rmse_rf}")
print(f"Gradient Boosting - R^2: {r2_gb}, MAE: {mae_gb}, MSE: {mse_gb}, RMSE: {rmse_gb}")


Linear Regression - R^2: 0.25121834623887884, MAE: 30.509764831673372, MSE: 1399.0220694458058, RMSE: 37.403503438124694
Random Forest - R^2: 0.19039682481837739, MAE: 31.82764043548629, MSE: 1512.6608723426755, RMSE: 38.89294116343833
Gradient Boosting - R^2: 0.19994717344160973, MAE: 31.688226363085978, MSE: 1494.8170210307603, RMSE: 38.66286359067006


Линейная регрессия: По всем метрикам (R^2, MAE, MSE, RMSE) линейная регрессия показывает лучшие результаты. Она объясняет большую часть вариации в данных и имеет наименьшие ошибки как в абсолютных величинах, так и в квадратных отклонениях.

Random Forest и Gradient Boosting: Эти модели показывают худшие результаты по сравнению с линейной регрессией, как по объяснению вариации данных, так и по величине ошибок.

#### Оценка смещения и дисперсии лучшей модели (линейная регрессия).

In [184]:
import numpy as np
from sklearn.model_selection import cross_val_predict, KFold
from sklearn.metrics import mean_squared_error

# Количество фолдов для кросс-валидации
n_splits = 5
kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)

# Прогнозы с использованием кросс-валидации с конвейером
y_pred = cross_val_predict(linear_pipeline, X_train, y_train.values.ravel(), cv=kf)

# Среднее значение целевой переменной
y_true_mean = np.mean(y_train)

# Смещение: разница между средним предсказанием модели и средним значением целевой переменной
bias = np.mean(y_pred) - y_true_mean

# Дисперсия: среднее отклонение предсказаний от среднего предсказания
variance = np.mean((y_pred - np.mean(y_pred)) ** 2)

# Средняя ошибка (для контекста)
mse = mean_squared_error(y_train, y_pred)
rmse = np.sqrt(mse)

# Выводим результаты
print(f"Смещение (Bias): {bias}")
print(f"Дисперсия (Variance): {variance}")
print(f"RMSE: {rmse}")


Смещение (Bias): 0.13896485197494712
Дисперсия (Variance): 432.34643616182956
RMSE: 37.95928016105437


Смещение и дисперсия вместе составляют основную часть ошибки модели. Смещение (bias) относительно невелико, но модель имеет достаточно высокую дисперсию. Это означает, что модель может страдать от переобучения (overfitting), то есть она слишком хорошо подгоняется под обучающие данные и не обобщает информацию на новые данные. В таких случаях модель может показывать хорошие результаты на обучающих данных, но её способность предсказывать для новых, невиданных данных может быть ограничена.

RMSE также указывает на наличие значительных ошибок в предсказаниях, и, вероятно, модель нуждается в улучшении. 